In [1]:
import os
import base64
import requests
from dotenv import load_dotenv

In [2]:
load_dotenv()

ACCOUNT_ID = os.environ["CLOUDFLARE_ACCOUNT_ID"]
API_TOKEN = os.environ["CLOUDFLARE_API_TOKEN"]

## Text to image

In [ ]:
# https://developers.cloudflare.com/workers-ai/models/flux-1-schnell/

MODEL = "@cf/black-forest-labs/flux-1-schnell"
URL = f"https://api.cloudflare.com/client/v4/accounts/{ACCOUNT_ID}/ai/run/{MODEL}"

payload = {
    "prompt": "cyborg crocodile, realistic style, single object, front and side fully visible, plain neutral background, clear details, soft studio lighting, true-to-scale",
}

headers = {
    "Authorization": f"Bearer {API_TOKEN}",
    "Content-Type": "application/json",
}

resp = requests.post(URL, json=payload, headers=headers, timeout=60)
resp.raise_for_status()

data = resp.json()
b64 = data["result"]["image"]
if not b64:
    raise RuntimeError(f"Unexpected response structure: {data}")

img_bytes = base64.b64decode(b64)

out_path = "test_resources/resolution_test_1.jpg"
with open(out_path, "wb") as f:
    f.write(img_bytes)

print(f"Saved: {out_path}  ({len(img_bytes)} bytes)")

Saved: test_resources/resolution_test_1.jpg  (315728 bytes)


## Text prompt refinement

In [13]:
MODEL = "@cf/meta/llama-3.2-3b-instruct"
URL = f"https://api.cloudflare.com/client/v4/accounts/{ACCOUNT_ID}/ai/run/{MODEL}"

instructions = """
User is talking about some object. Your task is to generate a short and concise description of it. Use only user's own words, keep it as short as possible.
Example:
User: 'Umm, okay, I would like a really cool sword, with for example a bright orange crossguard. And also it should be slightly curved.'
You: 'a slightly curved sword with bright orange crossguard'
"""
prompt = "Umm, alright, can you please give me an epic battleaxe? It should have a dark wooden shaft and bronze blade."

response = requests.post(URL,
  headers={"Authorization": f"Bearer {API_TOKEN}"},
  json={
    "messages": [
      {"role": "system", "content": instructions},
      {"role": "user", "content": prompt}
    ]
  }
)
data = response.json()
result_text = data["result"]["response"]
print(result_text)

"dark wooden battleaxe with bronze blade"
